# Transformer Vizualizations

In [1]:
# Imports
%matplotlib inline
from transformers import AutoTokenizer, AutoModel
from transformers import BertTokenizer, BertModel
from bertviz import head_view, model_view
import torch
from pdb import set_trace




# Last relative import
import os
import sys
module_path = os.path.abspath(os.path.join('../..'))
if module_path not in sys.path:
    sys.path.append(module_path)
from classifiers import TextClassificationBERT


In [2]:
# Set device
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

## BERT

### Head View

In [3]:
# Now with custom fine-tuned BERT_FT
bert_model = TextClassificationBERT(num_classes=2)
bert_model_path = '../../models/prompt_classifiers/bert_bnc_rb_ws_ca_seed_4_24_Sep_2021_BEST.pt'
bert_model.load_state_dict(torch.load(bert_model_path, map_location=device))
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased', truncation=True, max_length=500) 

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [7]:
def show_head_view(model, tokenizer, sentence_a, sentence_b=None, layer=None, heads=None, label=0):
    
    # convert label to tensor
    label = torch.tensor(label)
    
    # encode inputs using tokenizer and extract input IDs
    inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt', add_special_tokens=True)
    input_ids = inputs['input_ids']
    
    if sentence_b:
        token_type_ids = inputs['token_type_ids']
        attention = model(text=input_ids, label=label, bertviz=True, token_type_ids=token_type_ids)[-1]
        sentence_b_start = token_type_ids[0].tolist().index(1)
    else:
        attention = model(text=input_ids, label=label, bertviz=True)[-1]
        sentence_b_start = None
    input_id_list = input_ids[0].tolist() # Batch index 0
    tokens = tokenizer.convert_ids_to_tokens(input_id_list)
    head_view(attention, tokens, sentence_b_start, layer=layer, heads=heads)

In [8]:
model_version = 'bert-base-uncased'
do_lower_case = True
sentence_a = "Tell me about your latest holiday."
sentence_b = 'I visited my family in Greece.'
show_head_view(bert_model, bert_tokenizer, sentence_a, sentence_b, label=1)

<IPython.core.display.Javascript object>

### Model View

In [9]:
def show_model_view(model, tokenizer, sentence_a, sentence_b=None, hide_delimiter_attn=False, display_mode="dark", label=0):
    
    label = torch.tensor(label)
    
    inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt', add_special_tokens=True)
    input_ids = inputs['input_ids']
    if sentence_b:
        token_type_ids = inputs['token_type_ids']
        attention = model(text=input_ids, label=label, bertviz=True, token_type_ids=token_type_ids)[-1]
        sentence_b_start = token_type_ids[0].tolist().index(1)
    else:
        attention = model(text=input_ids, label=label, bertviz=True, token_type_ids=token_type_ids)[-1]
        sentence_b_start = None
    input_id_list = input_ids[0].tolist() # Batch index 0
    tokens = tokenizer.convert_ids_to_tokens(input_id_list)  
    if hide_delimiter_attn:
        for i, t in enumerate(tokens):
            if t in ("[SEP]", "[CLS]"):
                for layer_attn in attention:
                    layer_attn[0, :, i, :] = 0
                    layer_attn[0, :, :, i] = 0
    model_view(attention, tokens, sentence_b_start, display_mode=display_mode)
    
    return attention

In [10]:
model_version = 'bert-base-uncased'
do_lower_case = True
sentence_a = "The cat sat on the mat"
sentence_b = "The cat lay on the rug"
attention_without = show_model_view(bert_model, bert_tokenizer, sentence_a, sentence_b, hide_delimiter_attn=False, display_mode="dark")

<IPython.core.display.Javascript object>

## GPT-2

### Head View

### Model View